In [0]:
library(nnet)
banknote <- read.csv("http://www.sakurai.comp.ae.keio.ac.jp/classes/ML-class/2019/banknote.csv")
head(banknote)

In [0]:
# Let us find what are the values of target feater Y
table(banknote[,length(banknote)])

In [0]:
# Because Y is binary (i.e., (0,1)), the number of outputs can be just one with values 0 and 1
# (there could be two outputs)

# Because banknote is alread data.frame, we can use it as is
# let us try three hidden units
banknote.nn <- nnet( Y ~ ., banknote, size=3, maxit=1000)

In [0]:
source("http://www.sakurai.comp.ae.keio.ac.jp/classes/ML-class/2019/plot.nn.txt")
plot.nn(banknote.nn)

In [0]:
# confusion matrix
attach(banknote)
table(Y,apply(predict(banknote.nn),1,which.max))

In [0]:
# to search for a reason, let us look into distribution of feature values (should be done before)
summary(banknote)

In [0]:
# mean of columns
apply(banknote, 2,mean)

In [0]:
# standard deviation of columns
apply(banknote, 2, sd)

In [0]:
# Standard deviations are OK, but menas vary much.
# Therefore we will try to normalize the feature values.
# Note that target feature must not be normalized because they are categorical.
# If so, the code becomes a bit longer (but just one line longer)
# If all features are to be normalized
#    normalize <- function (x) (x - mean(x))/sd(x)
#    normalizedBanknote <- apply(banknote, 2, normalize)
# are enough.
# R built-in function "scale" may be used (use "scale" instead of "normalize")
normalize <- function (x) (x - mean(x))/sd(x)
tmp <- apply(banknote[,1:length(banknote)-1], 2, normalize)
normalizedBanknote <- cbind(data.frame(tmp), Y=banknote[,length(banknote)])

In [0]:
banknote.nn <- nnet( Y ~ ., normalizedBanknote, size=2, maxit=1000)
table( Y, round(predict(banknote.nn)) )

In [0]:
# too good
# may possibly be overtrained. Let us try 10-fold cross validation

In [0]:
install.packages("bootstrap")

In [0]:
library(bootstrap)               # for a function "crossval"

# functions to use crossval are to be defined
# Note: "2" in the next line is the number of hidden unit in nnet.
theta.fit <- function (x,y) { return( nnet( x, y, ,2  ) ) }
theta.predict <- function( fit, x) {predict( fit, data.frame(x)) }

# Now we can call "crossval"
xy <- normalizedBanknote   # just for abbreviation
results <- crossval(xy[,-length(xy)], xy[,length(xy)], theta.fit, theta.predict, ngroup=10) 

In [0]:
# confusion matrix 
(cm <- table( xy[,length(xy)], round( results$cv.fit )  ))

In [0]:
 # and accuracy
 (accuracy10CV <- sum(diag(cm))/sum(cm))